# Introducción

# Configuración

In [1]:
# Common imports
import numpy as np
import pandas as pd

#Plotting
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns

#Interactive plotting
import plotly
import plotly.graph_objects as go
from plotly.offline import download_plotlyjs, init_notebook_mode,  iplot
init_notebook_mode(connected=True)


#3D mesh API
#import pymesh

# MATLAB API
import matlab.engine

In [2]:
import io
from IPython.core.magic import register_cell_magic
ip = get_ipython()

out = io.StringIO()
err = io.StringIO()

# Setup matlab cell magic #
@register_cell_magic
def matlab_magic(line,cell):
    out.truncate(0)
    out.seek(0)
    err.truncate(0)
    err.truncate(0)
    raw = r'{line}.eval("""{cell}""", nargout=0, stdout=out, stderr=err)'
    ip.run_cell(raw.format(line=line, cell=cell))
    print(out.getvalue())
    print(err.getvalue())

In [3]:
eng = matlab.engine.start_matlab() # start matlab session
eng.eval("format compact", nargout=0) # compact formatting in matlab's stdout

In [4]:
def obj_data_to_mesh3d(odata):
    # odata is the string read from an obj file
    vertices = []
    faces = []
    lines = odata.splitlines()   
    
    for line in lines:
        slist = line.split()
        if slist:
            if slist[0] == 'v':
                vertex = np.array(slist[1:], dtype=float)
                vertices.append(vertex)
            elif slist[0] == 'f':
                face = []
                for k in range(1, len(slist)):
                    face.append([int(s) for s in slist[k].replace('//','/').split('/')])
                if len(face) > 3: # triangulate the n-polyonal face, n>3
                    faces.extend([[face[0][0]-1, face[k][0]-1, face[k+1][0]-1] for k in range(1, len(face)-1)])
                else:    
                    faces.append([face[j][0]-1 for j in range(len(face))])
            else: pass
    
    
    return np.array(vertices), np.array(faces) 

# TODO

In [5]:
%%matlab_magic eng

x = 5

x =
     5




In [6]:
eng.workspace['x']

5.0

In [82]:
a = matlab.double([1,4,9,16,25])

In [83]:
a

matlab.double([[1.0,4.0,9.0,16.0,25.0]])

In [84]:
b = np.array(a)
b

array([[ 1.,  4.,  9., 16., 25.]])

In [86]:
c = matlab.double(b.tolist())
c

matlab.double([[1.0,4.0,9.0,16.0,25.0]])

In [12]:
with open('IRB120.obj', 'r') as file:
    obj_data = file.read()

In [13]:
vertices, faces = obj_data_to_mesh3d(obj_data)

In [14]:
vertices.shape

(30955, 3)

In [15]:
faces.shape

(61376, 3)

In [19]:
x, y, z = vertices.T
I, J, K = faces.T

mesh = go.Mesh3d(
            x=x,
            y=y,
            z=z,                     
            i=I,
            j=J,
            k=K,
            name='',
            showscale=False)

In [17]:
layout = go.Layout(title='Mesh3d from a Wavefront obj file',
                   font=dict(size=14, color='black'),
                   width=900,
                   height=800,
                  paper_bgcolor='rgb(235,235,235)',
                  margin=dict(t=175)) 

In [18]:
fig = go.Figure(data=[mesh], layout=layout)
iplot(fig)